In [1]:
# @version : 05/2023
# @author : grafika_jati
# 2D Y,Z LiDAR pixelization

# get 2D pixel image by Y, Z projection approach
# Y and Z coordinate are normalized based on data train
# Training data is data taken from experiment #1,#2,#3,#4
# Testing Data is data taken from experiment #5
# Each pixel in 2D image has three channel X, R, A
# value in those channel also normalized based on X,R,A value over all contaminant and experiment in train data 


# Split train and test from dataset taken by # B. Schlager, T. Goelles, S. Muckenhuber and D. Watzenig, "Contaminations on Lidar Sensor Covers: Performance Degradation Including Fault Detection and Modeling as Potential Applications," in IEEE Open Journal of Intelligent Transportation Systems, vol. 3, pp. 738-747, 2022, doi: 10.1109/OJITS.2022.3214094.

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "cuda:3"

from pathlib import Path
import os
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

# import pointcloudset as pcs
import pointcloudset.dataset as pcs #problem running all gpu
import torch

# if torch.cuda.is_available():
#   dev = "cuda:3"
#   print("yey")
# device = torch.device(dev)

print("Create 2D pixel image of 3D Lidar Data")

Create 2D pixel image for Lidar Data


In [3]:
def lidar_to_2d_front_view(points, r_min, r_range, a_min, a_range, x_min, y_min, z_min, x_max, y_max, z_max, xyz_spacing,num_channel, pixel_size):


    x_lidar = points[:, 0]
    y_lidar = points[:, 1]
    z_lidar = points[:, 2]
    # i_lidar = points[:, 3] # intensity , uncomment this line if use intensity
    r_lidar = points[:, 3] # reflectivity
    a_lidar = points[:, 4] # ambient


    #normalized coordinate
    x_min_arr=np.empty(len(x_lidar))
    x_min_arr.fill(x_min)

    y_min_arr=np.empty(len(y_lidar))
    y_min_arr.fill(y_min)

    z_min_arr=np.empty(len(z_lidar))
    z_min_arr.fill(z_min)

    x_max_arr=np.empty(len(x_lidar))
    x_max_arr.fill(x_max)

    y_max_arr=np.empty(len(y_lidar))
    y_max_arr.fill(y_max)

    z_max_arr=np.empty(len(z_lidar))
    z_max_arr.fill(z_max)


    # Normalization
    x_lidar_norm =  (x_lidar - x_min_arr)/(x_max_arr - x_min_arr)
    y_lidar_norm =  (y_lidar - y_min_arr)/(y_max_arr - y_min_arr)
    z_lidar_norm =  (z_lidar - z_min_arr)/(z_max_arr - z_min_arr)


    y_grid_spacing=[]
    y_grid_spacing = [xyz_spacing for i in range(len(y_lidar))] 

    z_grid_spacing=[]
    z_grid_spacing = [xyz_spacing for i in range(len(z_lidar))] 


    # Pixelization
    # x_lidar_norm = np.round(x_lidar_norm / x_grid_spacing) # X as value / feature. it is not discritized 
    y_lidar_norm = np.round(y_lidar_norm  / y_grid_spacing)
    z_lidar_norm = np.round(z_lidar_norm / z_grid_spacing)
    
    # get mean value for poin in same cluster or same coordinate
    arr_check = np.zeros([len(y_lidar_norm),2]) # array to check if a point that have same coordinate position with other points, If some point projected in same coordinate, then we calculate mean value of feature from each point in the same cluster (coordinate)
    #assign each new coordinate from each point
    for i in range(len(y_lidar_norm)):
        arr_check[i][0]=y_lidar_norm[i]
        arr_check[i][1]=z_lidar_norm[i]

    uniqueRows = np.unique(arr_check, axis=0) # check unique coordinate

    list_cluster=[[] for i in range(len(uniqueRows))] # list to save cluster of same coordinate
    for i in range(len(uniqueRows)):
        n=0
        for j in range(len(arr_check)):
            if (uniqueRows[i]==arr_check[j]).all():
            # print(j)
                list_cluster[i].append(j) # put average value to this pixel coordinate
                n=n+1

    x_lidar_cluster=x_lidar_norm.copy()
    # i_lidar_cluster=i_lidar.copy()
    r_lidar_cluster=r_lidar.copy() 
    a_lidar_cluster=a_lidar.copy()


    #check mean if same coordinate
    #assign mean as new value
    for i in range(len(list_cluster)):
        x_temp_mean=0
        # i_temp_mean=0
        r_temp_mean=0
        a_temp_mean=0
        
        for j in range(len(list_cluster[i])):
            x_temp_mean += x_lidar_norm[list_cluster[i][j]]
            # i_temp_mean += i_lidar[list_cluster[i][j]]
            r_temp_mean += r_lidar[list_cluster[i][j]]
            a_temp_mean += a_lidar[list_cluster[i][j]]
                
        x_temp_mean=x_temp_mean/len(list_cluster[i])
        # i_temp_mean=i_temp_mean/len(list_cluster[i])
        r_temp_mean=r_temp_mean/len(list_cluster[i])
        a_temp_mean=a_temp_mean/len(list_cluster[i])

            
        # print(temp_mean)
        for j in range(len(list_cluster[i])):
            x_lidar_cluster[list_cluster[i][j]]=x_temp_mean
            # i_lidar_cluster[list_cluster[i][j]]=i_temp_mean
            r_lidar_cluster[list_cluster[i][j]]=r_temp_mean
            a_lidar_cluster[list_cluster[i][j]]=a_temp_mean



    arr_single_img = np.zeros([num_channel, int(pixel_size), int(pixel_size)]) #  channel, row, coloumn


    for k in range(len(x_lidar_cluster)): # Outer loop  
        arr_single_img[0][int(y_lidar_norm[k])][int(z_lidar_norm[k])]=x_lidar_cluster[k]
        # arr_single_img[1][int(y_lidar_norm[k])][int(z_lidar_norm[k])]=i_lidar_cluster[k]
        arr_single_img[1][int(y_lidar_norm[k])][int(z_lidar_norm[k])]=(r_lidar_cluster[k] - r_min) / r_range
        arr_single_img[2][int(y_lidar_norm[k])][int(z_lidar_norm[k])]=(a_lidar_cluster[k] - a_min) / a_range

       
    return arr_single_img

In [4]:
rootdir = "../Dataset/ouster_OS1-64_point_clouds_filter_data" # filter means only experiment that has point clouds 

print("tes read lidar data All- each points per experiment")


# constant parameter to normalized coordinate and attribute
# That value is taken from Dataset exp 1,2,3,4 over all type of contamiant 
# do normalization for testing dataset (exp 5) using value from training dataset

x_min = 8.136452 # minimum coordinate point in x-axis
y_min = -0.313579 # minimum coordinate point in y-axis
z_min = -0.260452 # minimum coordinate point in z-axis

x_max = 8.992307 # maximum coordinate point in x-axis
y_max = 0.499952 # maximum coordinate point in y-axis
z_max = 0.145646 # maximum coordinate point in z-axis


a_min = 0.0 # minimun value of ambient
r_min = 59.0 # minimun value of reflectivity

a_max = 472.0 # maximum value of ambient
r_max = 19528.0 # maximum value of reflectivity

a_range = a_max-a_min # minimun value of ambient
r_range = r_max-r_min # range value of reflectivity

# spacing parameter for pixelization
# xyz_spacing = 0.01 # produce 2d image with size 101x101 
xyz_spacing = 0.1 # produce 2d image with size 11x11 
# xyz_spacing = 0.02 # produce 2d image with size 51x51 

num_channel = 3 # number of channel for each 2d image. 3 : X, Reflectivity, Ambient
pixel_size = 11 # size of projected 2D image

		
# each dir create an array
df_temp = pd.DataFrame()
df_temp = pd.DataFrame(columns = ['class', 'exp', 'data'])

for dirs in os.listdir(rootdir):
	n=0
	temp_dir=str(rootdir+"/"+dirs)
	# print(dirs)

	name = dirs.split('_')
	name_temp= name[2] # get name of contaminant

	contaminant_type=name_temp[:-1] # remove number of experiment
	exp=name_temp[-1]
	
	if contaminant_type=="reference-with-cove":
		contaminant_type="cover"
		exp=1
		
	elif contaminant_type=="reference-without-cove":
		contaminant_type="no_cover"
		exp=1

	elif contaminant_type=="artificial-dirt-05m":
		contaminant_type="dirt_05mm"
		exp=1

	elif contaminant_type=="artificial-dirt-10m":
		contaminant_type="dirt_10mm"
		exp=1

	elif contaminant_type=="artificial-dirt-15m":
		contaminant_type="dirt_15mm"
		exp=1


	for filename in os.listdir(temp_dir):
	# print("filename")
	# print(filename)

		if filename.endswith(".parquet"): #check if lidar data is exist
        
			ouster_data = pcs.Dataset.from_file(Path("../Dataset/ouster_OS1-64_point_clouds_filter_data/"+str(dirs)))
			df_points = ouster_data[n].data[["x","y","z", "reflectivity", "ambient"]]
			
			if not df_points.empty:
				# print('DataFrame is empty!')

				lidar= df_points.to_numpy()

			#get single image of lidar per contaminant and experiment
				single_img_lidar = lidar_to_2d_front_view(lidar, r_min, r_range, a_min, a_range, x_min, y_min, z_min, x_max, y_max, z_max, xyz_spacing, num_channel, pixel_size)

				df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
    
			n=n+1


df_temp.to_json('lidar_norm_train_test_2d_pixel_6class_norm_XRA_10x10.json')



tes read lidar data All- each points per experiment


/tmp/ipykernel_784425/1203709142.py:98: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_784425/1203709142.py:98: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_784425/1203709142.py:98: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_784425/1203709142.py:98: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a fut